In [1]:
# install dependencies: 
!pip install pyyaml==5.1 pycocotools>=2.0.1


In [ ]:
from google_drive_downloader import GoogleDriveDownloader as gdd

gdd.download_file_from_google_drive(file_id='1BqUGCLrtoPIw_xyYh4rOZLwTVOX7p6Y3',
                                    dest_path='/content/dfg_aug_labels.zip',
                                    unzip=True)


In [2]:

annotation_file="/home/iav/code/trafficsign/dfg/labels/train_difficult_dfg.json"
# annotation_file="/content/test.json"

In [4]:
# Initialize the COCO api for instance annotations
from pycocotools.coco import COCO

coco=COCO(annotation_file)

cat_dict={}
cat_names=[]
labels_statistics={k:0 for k in range(1,201)}
labels_contents={k:[] for k in range(1,201)}

catIDs = coco.getCatIds()
cat_contents = coco.loadCats(catIDs)
imageIDs=coco.getImgIds()
images_contents=coco.loadImgs(imageIDs)
annIDs=coco.getAnnIds() 
ann_contents=coco.loadAnns(annIDs)
total_ann_num=len(ann_contents)

for i in range(len(cat_contents)):
  cat_dict[cat_contents[i]["id"]]=cat_contents[i]["name"]
  cat_names.append(cat_contents[i]["name"])

for item in ann_contents:
  labels_statistics[item["category_id"]]+=1
  labels_contents[item["category_id"]].append(item)

# cat_dict
# cat_names
# labels_statistics
# total_ann_num
# labels_contents
# images_contents
# ann_contents

loading annotations into memory...
Done (t=0.29s)
creating index...
index created!


In [9]:
import random
labels_sample_statistics={k:0 for k in range(1,201)}
labels_sample_contents={k:[] for k in range(1,201)}
total_sample_num=0
filteredImgIds=dict()

for a in range(1,201):
  sample_num=round(labels_statistics.get(a)*0.03)
  labels_sample_statistics[a]=sample_num
  total_sample_num+=sample_num
  random_sample=random.sample(labels_contents[a],sample_num)
  labels_sample_contents[a].append(random_sample)
  for b in random_sample:
    images_content=coco.loadImgs(b["image_id"])
    filteredImgIds[b["image_id"]]=images_content

# labels_sample_contents
len(filteredImgIds)

1269

In [10]:
images = list()
annotations = list()

file_name_dict=dict()
id_count=0
image_count=1
new_Img_contents=list()

for e in filteredImgIds.keys():
  for f in ann_contents:
    if f["image_id"]==e:
      # print(f)
      newImg_content=dict()
      annotation = dict()
      annotation['id'] = id_count
      annotation["iscrowd"] = f["iscrowd"]

      img_content=filteredImgIds[e][0]
      # print(img_content)
      if img_content["file_name"] in file_name_dict.keys():
        new_image_id=file_name_dict[img_content["file_name"]]["id"]
      else:
        newImg_content["file_name"]=img_content["file_name"]
        newImg_content["height"]=img_content["height"]
        newImg_content["width"]=img_content["width"]
        newImg_content["id"]=image_count
        # print(newImg_content)
        file_name_dict[img_content["file_name"]]=newImg_content
        new_image_id=image_count
        new_Img_contents.append(newImg_content)
        image_count+=1

      annotation["image_id"] = new_image_id
      annotation['bbox'] = f['bbox']
      annotation['area'] = f['area']
      annotation['category_id'] = f['category_id']
#       if f['ignore']=="false":
#         annotation['ignore'] = 0
#       else:
#         annotation['ignore'] = 1
      annotation['segmentation'] = f['segmentation']
#       print(id_count)
      id_count+=1
      annotations.append(annotation)
print("number of annotations",len(annotations))    
print("number of images",len(new_Img_contents))    

# annotations
# new_Img_contents      




number of annotations 4818
number of images 1269


In [11]:
import json
dataset = json.load(open(annotation_file, 'r'))
categories=dataset['categories']
print(categories)

[{'id': 200, 'name': 'I-1', 'supercategory': 'traffic_sign'}, {'id': 1, 'name': 'I-1.1', 'supercategory': 'traffic_sign'}, {'id': 2, 'name': 'I-10', 'supercategory': 'traffic_sign'}, {'id': 3, 'name': 'I-11', 'supercategory': 'traffic_sign'}, {'id': 4, 'name': 'I-13', 'supercategory': 'traffic_sign'}, {'id': 5, 'name': 'I-13.1', 'supercategory': 'traffic_sign'}, {'id': 6, 'name': 'I-14', 'supercategory': 'traffic_sign'}, {'id': 7, 'name': 'I-15', 'supercategory': 'traffic_sign'}, {'id': 8, 'name': 'I-16', 'supercategory': 'traffic_sign'}, {'id': 9, 'name': 'I-17', 'supercategory': 'traffic_sign'}, {'id': 10, 'name': 'I-18', 'supercategory': 'traffic_sign'}, {'id': 11, 'name': 'I-19', 'supercategory': 'traffic_sign'}, {'id': 12, 'name': 'I-2', 'supercategory': 'traffic_sign'}, {'id': 13, 'name': 'I-2.1', 'supercategory': 'traffic_sign'}, {'id': 14, 'name': 'I-20', 'supercategory': 'traffic_sign'}, {'id': 15, 'name': 'I-25', 'supercategory': 'traffic_sign'}, {'id': 16, 'name': 'I-27', 's

In [12]:

def coco_generation(attr_dict, images_contents,annotations,fn):

    
    attr_dict["images"] = new_Img_contents
    attr_dict["categories"] = categories
    attr_dict["annotations"] = annotations
    attr_dict["info"] = {"contributor":"william","description":"test","date_created":"0915","year":2020,"version":1}

    print('saving...')
    json_string = json.dumps(attr_dict)
    with open(fn, "w") as file:
        file.write(json_string)
    print('finish coco subeset sample generation')

if __name__ == '__main__':

    # create subset training set in COCO format
    attr_dict=dict()
    out_fn='/home/iav/code/trafficsign/dfg/labels/subset_train.json'
    coco_generation(attr_dict, images_contents,annotations,out_fn)


saving...
finish coco subeset sample generation


In [13]:

new_coco=COCO(out_fn)

new_labels_statistics={k:0 for k in range(1,201)}

new_annIDs=new_coco.getAnnIds() 
new_ann_contents=new_coco.loadAnns(new_annIDs)
print(len(new_ann_contents))

for item in new_ann_contents:
  new_labels_statistics[item["category_id"]]+=1
new_labels_statistics

loading annotations into memory...
Done (t=0.03s)
creating index...
index created!
4818


{1: 15,
 2: 20,
 3: 24,
 4: 21,
 5: 23,
 6: 18,
 7: 25,
 8: 22,
 9: 17,
 10: 17,
 11: 19,
 12: 22,
 13: 24,
 14: 26,
 15: 28,
 16: 30,
 17: 21,
 18: 22,
 19: 19,
 20: 24,
 21: 15,
 22: 26,
 23: 18,
 24: 20,
 25: 18,
 26: 25,
 27: 21,
 28: 19,
 29: 21,
 30: 20,
 31: 18,
 32: 16,
 33: 23,
 34: 17,
 35: 22,
 36: 22,
 37: 67,
 38: 21,
 39: 21,
 40: 25,
 41: 18,
 42: 26,
 43: 33,
 44: 18,
 45: 15,
 46: 16,
 47: 29,
 48: 27,
 49: 25,
 50: 33,
 51: 20,
 52: 21,
 53: 25,
 54: 23,
 55: 28,
 56: 21,
 57: 21,
 58: 16,
 59: 24,
 60: 21,
 61: 17,
 62: 27,
 63: 24,
 64: 18,
 65: 24,
 66: 18,
 67: 23,
 68: 27,
 69: 34,
 70: 22,
 71: 23,
 72: 19,
 73: 24,
 74: 40,
 75: 20,
 76: 41,
 77: 26,
 78: 26,
 79: 18,
 80: 21,
 81: 14,
 82: 22,
 83: 26,
 84: 28,
 85: 16,
 86: 49,
 87: 20,
 88: 21,
 89: 20,
 90: 28,
 91: 20,
 92: 14,
 93: 19,
 94: 22,
 95: 36,
 96: 20,
 97: 17,
 98: 19,
 99: 21,
 100: 29,
 101: 20,
 102: 23,
 103: 17,
 104: 22,
 105: 19,
 106: 20,
 107: 25,
 108: 22,
 109: 20,
 110: 15,
 111: 26

In [15]:
!PYTHONPATH=".:$PYTHONPATH"  python dataset/create_coco_tfrecord.py  \
    --image_dir=/home/iav/code/trafficsign/dfg/JPEGImages \
    --object_annotations_file=/home/iav/code/trafficsign/dfg/labels/subset_train.json \
    --output_file_prefix=/home/iav/code/bigdata/dfg_efficientdet/train_subset_tfrecord/train \
    --num_shards=4

2020-09-22 09:35:52.255035: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcudart.so.10.1
I0922 09:35:53.239899 140191193368384 create_coco_tfrecord.py:285] writing to output path: /home/iav/code/bigdata/dfg_efficientdet/train_subset_tfrecord/train
I0922 09:35:53.817965 140191193368384 create_coco_tfrecord.py:215] Building bounding box index.
I0922 09:35:53.876099 140191193368384 create_coco_tfrecord.py:226] 0 images are missing bboxes.
I0922 09:35:53.965840 140191193368384 create_coco_tfrecord.py:323] On image 0 of 1269
I0922 09:35:54.024698 140191193368384 create_coco_tfrecord.py:323] On image 100 of 1269
I0922 09:35:54.108561 140191193368384 create_coco_tfrecord.py:323] On image 200 of 1269
I0922 09:35:54.177312 140191193368384 create_coco_tfrecord.py:323] On image 300 of 1269
I0922 09:35:54.257338 140191193368384 create_coco_tfrecord.py:323] On image 400 of 1269
I0922 09:35:54.333058 140191193368384 create_coco_tfrecord.py:323

In [16]:
!PYTHONPATH=".:$PYTHONPATH"  python dataset/create_coco_tfrecord.py  \
    --image_dir=/home/iav/code/trafficsign/dfg/JPEGImages \
    --object_annotations_file=/home/iav/code/trafficsign/dfg/labels/test_dfg.json \
    --output_file_prefix=/home/iav/code/bigdata/dfg_efficientdet/test_tfrecord/test \
    --num_shards=4

2020-09-22 09:42:51.627647: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcudart.so.10.1
I0922 09:42:52.611569 140006098675520 create_coco_tfrecord.py:285] writing to output path: /home/iav/code/bigdata/dfg_efficientdet/test_tfrecord/test
I0922 09:42:52.653243 140006098675520 create_coco_tfrecord.py:215] Building bounding box index.
I0922 09:42:52.654463 140006098675520 create_coco_tfrecord.py:226] 0 images are missing bboxes.
I0922 09:42:52.955519 140006098675520 create_coco_tfrecord.py:323] On image 0 of 1703
I0922 09:42:53.083387 140006098675520 create_coco_tfrecord.py:323] On image 100 of 1703
I0922 09:42:53.216366 140006098675520 create_coco_tfrecord.py:323] On image 200 of 1703
I0922 09:42:53.355047 140006098675520 create_coco_tfrecord.py:323] On image 300 of 1703
I0922 09:42:53.491029 140006098675520 create_coco_tfrecord.py:323] On image 400 of 1703
I0922 09:42:53.616903 140006098675520 create_coco_tfrecord.py:323] On imag

In [18]:
d="d3"
times="dfg_subset_1"
# !rm -r /home/iav/code/williamhyin_automl/efficientdet/tmp/{d}_{times} 
!mkdir /home/iav/code/williamhyin_automl/efficientdet/tmp/{d}_{times} 
!python main.py --mode=train\
    --training_file_pattern=/home/iav/code/bigdata/dfg_efficientdet/train_subset_tfrecord/train* \
    --model_name=efficientdet-{d} \
    --model_dir=/home/iav/code/williamhyin_automl/efficientdet/tmp/{d}_{times}  \
    --ckpt=/home/iav/code/williamhyin_automl/efficientdet/weights/efficientdet-{d}  \
    --train_batch_size=2 \
    --num_examples_per_epoch=1269 --num_epochs=300  \
    --hparams=/home/iav/code/williamhyin_automl/efficientdet/configs/dfg_d3_subset.yaml \
    --save_checkpoints_steps=500 \

2020-09-22 09:48:08.811047: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcudart.so.10.1
I0922 09:48:10.063195 140366660470592 main.py:227] {'name': 'efficientdet-d3', 'act_type': 'swish', 'image_size': (896, 896), 'target_size': None, 'input_rand_hflip': True, 'jitter_min': 0.1, 'jitter_max': 2.0, 'autoaugment_policy': None, 'use_augmix': False, 'augmix_params': [3, -1, 1], 'sample_image': None, 'num_classes': 201, 'seg_num_classes': 3, 'heads': ['object_detection'], 'skip_crowd_during_training': True, 'label_map': {0: 'background', 1: 'I-1.1', 2: 'I-10', 3: 'I-11', 4: 'I-13', 5: 'I-13.1', 6: 'I-14', 7: 'I-15', 8: 'I-16', 9: 'I-17', 10: 'I-18', 11: 'I-19', 12: 'I-2', 13: 'I-2.1', 14: 'I-20', 15: 'I-25', 16: 'I-27', 17: 'I-28', 18: 'I-28.1', 19: 'I-29', 20: 'I-29.1', 21: 'I-3', 22: 'I-30', 23: 'I-32', 24: 'I-34', 25: 'I-36', 26: 'I-37', 27: 'I-38', 28: 'I-39-1', 29: 'I-39-2', 30: 'I-39-3', 31: 'I-4', 32: 'I-5', 33: 'I-5.1', 34: '

2020-09-22 09:48:10.154623: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcusparse.so.10
2020-09-22 09:48:10.157371: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcudnn.so.7
2020-09-22 09:48:10.158165: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1858] Adding visible gpu devices: 0
I0922 09:48:10.338692 140366660470592 dataloader.py:83] target_size = (896, 896), output_size = (896, 896)
INFO:tensorflow:Calling model_fn.
I0922 09:48:10.587759 140366660470592 estimator.py:1162] Calling model_fn.
I0922 09:48:10.587950 140366660470592 utils.py:422] Adding image summary ('input_image', <tf.Tensor 'IteratorGetNext:0' shape=(2, 896, 896, 3) dtype=float32>)
I0922 09:48:10.588257 140366660470592 utils.py:635] use mixed precision policy name mixed_float16
INFO:tensorflow:Mixed precision compatibility check (mixed_float16): OK
Your GPU will likely run quickly with dtype policy m

I0922 09:48:10.981358 140366660470592 efficientnet_model.py:195] Built SE se : (2, 1, 1, 24)
I0922 09:48:11.004748 140366660470592 efficientnet_model.py:412] Project shape: (2, 448, 448, 24)
I0922 09:48:11.005074 140366660470592 efficientnet_model.py:738] block_2 survival_prob: 0.9846153846153847
I0922 09:48:11.005383 140366660470592 efficientnet_model.py:372] Block blocks_2 input shape: (2, 448, 448, 24)
I0922 09:48:11.102337 140366660470592 efficientnet_model.py:388] Expand shape: (2, 448, 448, 144)
I0922 09:48:11.122141 140366660470592 efficientnet_model.py:391] DWConv shape: (2, 224, 224, 144)
I0922 09:48:11.138725 140366660470592 efficientnet_model.py:195] Built SE se : (2, 1, 1, 144)
I0922 09:48:11.158008 140366660470592 efficientnet_model.py:412] Project shape: (2, 224, 224, 32)
I0922 09:48:11.158294 140366660470592 efficientnet_model.py:738] block_3 survival_prob: 0.9769230769230769
I0922 09:48:11.158584 140366660470592 efficientnet_model.py:372] Block blocks_3 input shape: (2,

I0922 09:48:12.161804 140366660470592 efficientnet_model.py:195] Built SE se : (2, 1, 1, 816)
I0922 09:48:12.183953 140366660470592 efficientnet_model.py:412] Project shape: (2, 56, 56, 136)
I0922 09:48:12.184230 140366660470592 efficientnet_model.py:738] block_16 survival_prob: 0.8769230769230769
I0922 09:48:12.184514 140366660470592 efficientnet_model.py:372] Block blocks_16 input shape: (2, 56, 56, 136)
I0922 09:48:12.203850 140366660470592 efficientnet_model.py:388] Expand shape: (2, 56, 56, 816)
I0922 09:48:12.223562 140366660470592 efficientnet_model.py:391] DWConv shape: (2, 56, 56, 816)
I0922 09:48:12.240504 140366660470592 efficientnet_model.py:195] Built SE se : (2, 1, 1, 816)
I0922 09:48:12.263056 140366660470592 efficientnet_model.py:412] Project shape: (2, 56, 56, 136)
I0922 09:48:12.263331 140366660470592 efficientnet_model.py:738] block_17 survival_prob: 0.8692307692307693
I0922 09:48:12.263609 140366660470592 efficientnet_model.py:372] Block blocks_17 input shape: (2, 5

Instructions for updating:
Use keras.layers.MaxPooling2D instead.
W0922 09:48:13.646401 140366660470592 deprecation.py:323] From /home/iav/code/williamhyin_automl/efficientdet/efficientdet_arch.py:112: max_pooling2d (from tensorflow.python.keras.legacy_tf_layers.pooling) is deprecated and will be removed in a future version.
Instructions for updating:
Use keras.layers.MaxPooling2D instead.
I0922 09:48:13.651413 140366660470592 efficientdet_arch.py:399] building cell 0
I0922 09:48:13.651618 140366660470592 efficientdet_arch.py:490] fnode 0 : {'feat_level': 6, 'inputs_offsets': [3, 4]}
Instructions for updating:
Use `tf.keras.layers.SeparableConv2D` instead.
W0922 09:48:13.661697 140366660470592 deprecation.py:323] From /home/iav/code/williamhyin_automl/efficientdet/efficientdet_arch.py:525: separable_conv2d (from tensorflow.python.keras.legacy_tf_layers.convolutional) is deprecated and will be removed in a future version.
Instructions for updating:
Use `tf.keras.layers.SeparableConv2D` 

...

INFO:tensorflow:Calling checkpoint listeners before saving checkpoint 185500...
I0923 01:43:00.527495 140366660470592 basic_session_run_hooks.py:614] Calling checkpoint listeners before saving checkpoint 185500...
INFO:tensorflow:Saving checkpoints for 185500 into /home/iav/code/williamhyin_automl/efficientdet/tmp/d3_dfg_subset_1/model.ckpt.
I0923 01:43:00.527800 140366660470592 basic_session_run_hooks.py:618] Saving checkpoints for 185500 into /home/iav/code/williamhyin_automl/efficientdet/tmp/d3_dfg_subset_1/model.ckpt.
INFO:tensorflow:Calling checkpoint listeners after saving checkpoint 185500...
I0923 01:43:04.525561 140366660470592 basic_session_run_hooks.py:626] Calling checkpoint listeners after saving checkpoint 185500...
INFO:tensorflow:global_step/sec: 2.94196
I0923 01:43:04.864323 140366660470592 basic_session_run_hooks.py:702] global_step/sec: 2.94196
INFO:tensorflow:loss = 0.5898882, step = 185500 (33.993 sec)
I0923 01:43:04.867726 140366660470592 basic_session_run_hooks.p

INFO:tensorflow:global_step/sec: 3.33757
I0923 01:48:42.984711 140366660470592 basic_session_run_hooks.py:702] global_step/sec: 3.33757
INFO:tensorflow:loss = 0.4829735, step = 186600 (29.960 sec)
I0923 01:48:42.985967 140366660470592 basic_session_run_hooks.py:260] loss = 0.4829735, step = 186600 (29.960 sec)
INFO:tensorflow:box_loss = 0.00022020347, cls_loss = 0.3291456, det_loss = 0.34015578, step = 186600 (29.960 sec)
I0923 01:48:42.986351 140366660470592 basic_session_run_hooks.py:260] box_loss = 0.00022020347, cls_loss = 0.3291456, det_loss = 0.34015578, step = 186600 (29.960 sec)
INFO:tensorflow:global_step/sec: 3.30428
I0923 01:49:13.248487 140366660470592 basic_session_run_hooks.py:702] global_step/sec: 3.30428
INFO:tensorflow:loss = 0.8339416, step = 186700 (30.264 sec)
I0923 01:49:13.249638 140366660470592 basic_session_run_hooks.py:260] loss = 0.8339416, step = 186700 (30.264 sec)
INFO:tensorflow:box_loss = 0.0017234688, cls_loss = 0.6049505, det_loss = 0.6911239, step = 18

INFO:tensorflow:global_step/sec: 3.34504
I0923 01:54:51.737901 140366660470592 basic_session_run_hooks.py:702] global_step/sec: 3.34504
INFO:tensorflow:loss = 0.67215514, step = 187800 (29.895 sec)
I0923 01:54:51.739180 140366660470592 basic_session_run_hooks.py:260] loss = 0.67215514, step = 187800 (29.895 sec)
INFO:tensorflow:box_loss = 0.00061123923, cls_loss = 0.49877545, det_loss = 0.5293374, step = 187800 (29.895 sec)
I0923 01:54:51.739542 140366660470592 basic_session_run_hooks.py:260] box_loss = 0.00061123923, cls_loss = 0.49877545, det_loss = 0.5293374, step = 187800 (29.895 sec)
INFO:tensorflow:global_step/sec: 3.32274
I0923 01:55:21.833551 140366660470592 basic_session_run_hooks.py:702] global_step/sec: 3.32274
INFO:tensorflow:loss = 0.5387378, step = 187900 (30.096 sec)
I0923 01:55:21.834782 140366660470592 basic_session_run_hooks.py:260] loss = 0.5387378, step = 187900 (30.096 sec)
INFO:tensorflow:box_loss = 0.00036637887, cls_loss = 0.37760115, det_loss = 0.3959201, step 

INFO:tensorflow:Calling checkpoint listeners before saving checkpoint 189000...
I0923 02:00:59.717932 140366660470592 basic_session_run_hooks.py:614] Calling checkpoint listeners before saving checkpoint 189000...
INFO:tensorflow:Saving checkpoints for 189000 into /home/iav/code/williamhyin_automl/efficientdet/tmp/d3_dfg_subset_1/model.ckpt.
I0923 02:00:59.718217 140366660470592 basic_session_run_hooks.py:618] Saving checkpoints for 189000 into /home/iav/code/williamhyin_automl/efficientdet/tmp/d3_dfg_subset_1/model.ckpt.
INFO:tensorflow:Calling checkpoint listeners after saving checkpoint 189000...
I0923 02:01:03.741118 140366660470592 basic_session_run_hooks.py:626] Calling checkpoint listeners after saving checkpoint 189000...
INFO:tensorflow:global_step/sec: 2.93341
I0923 02:01:04.073962 140366660470592 basic_session_run_hooks.py:702] global_step/sec: 2.93341
INFO:tensorflow:loss = 0.73659635, step = 189000 (34.092 sec)
I0923 02:01:04.076888 140366660470592 basic_session_run_hooks.

INFO:tensorflow:global_step/sec: 3.31673
I0923 02:06:42.395136 140366660470592 basic_session_run_hooks.py:702] global_step/sec: 3.31673
INFO:tensorflow:loss = 0.5127431, step = 190100 (30.148 sec)
I0923 02:06:42.396345 140366660470592 basic_session_run_hooks.py:260] loss = 0.5127431, step = 190100 (30.148 sec)
INFO:tensorflow:box_loss = 0.0001876443, cls_loss = 0.36054322, det_loss = 0.36992544, step = 190100 (30.148 sec)
I0923 02:06:42.396713 140366660470592 basic_session_run_hooks.py:260] box_loss = 0.0001876443, cls_loss = 0.36054322, det_loss = 0.36992544, step = 190100 (30.148 sec)
INFO:tensorflow:global_step/sec: 3.33964
I0923 02:07:12.338441 140366660470592 basic_session_run_hooks.py:702] global_step/sec: 3.33964
INFO:tensorflow:loss = 0.5222317, step = 190200 (29.943 sec)
I0923 02:07:12.339707 140366660470592 basic_session_run_hooks.py:260] loss = 0.5222317, step = 190200 (29.943 sec)
INFO:tensorflow:box_loss = 0.0003416943, cls_loss = 0.36232924, det_loss = 0.37941396, step = 

In [19]:
d="d3"
times="dfg_subset_adam"
# !rm -r /home/iav/code/williamhyin_automl/efficientdet/tmp/{d}_{times} 
!mkdir /home/iav/code/williamhyin_automl/efficientdet/tmp/{d}_{times} 
!python main.py --mode=train\
    --training_file_pattern=/home/iav/code/bigdata/dfg_efficientdet/train_subset_tfrecord/train* \
    --model_name=efficientdet-{d} \
    --model_dir=/home/iav/code/williamhyin_automl/efficientdet/tmp/{d}_{times}  \
    --ckpt=/home/iav/code/williamhyin_automl/efficientdet/weights/efficientdet-{d}  \
    --train_batch_size=2 \
    --num_examples_per_epoch=1269 --num_epochs=300  \
    --hparams=/home/iav/code/williamhyin_automl/efficientdet/configs/dfg_d3_adam.yaml \
    --save_checkpoints_steps=500 \

2020-09-23 11:56:43.803939: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcudart.so.10.1
I0923 11:56:45.066594 140453499561792 main.py:227] {'name': 'efficientdet-d3', 'act_type': 'swish', 'image_size': (896, 896), 'target_size': None, 'input_rand_hflip': True, 'jitter_min': 0.1, 'jitter_max': 2.0, 'autoaugment_policy': None, 'use_augmix': False, 'augmix_params': [3, -1, 1], 'sample_image': None, 'num_classes': 201, 'seg_num_classes': 3, 'heads': ['object_detection'], 'skip_crowd_during_training': True, 'label_map': {0: 'background', 1: 'I-1.1', 2: 'I-10', 3: 'I-11', 4: 'I-13', 5: 'I-13.1', 6: 'I-14', 7: 'I-15', 8: 'I-16', 9: 'I-17', 10: 'I-18', 11: 'I-19', 12: 'I-2', 13: 'I-2.1', 14: 'I-20', 15: 'I-25', 16: 'I-27', 17: 'I-28', 18: 'I-28.1', 19: 'I-29', 20: 'I-29.1', 21: 'I-3', 22: 'I-30', 23: 'I-32', 24: 'I-34', 25: 'I-36', 26: 'I-37', 27: 'I-38', 28: 'I-39-1', 29: 'I-39-2', 30: 'I-39-3', 31: 'I-4', 32: 'I-5', 33: 'I-5.1', 34: '

2020-09-23 11:56:45.165402: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1716] Found device 0 with properties: 
pciBusID: 0000:21:00.0 name: GeForce RTX 2080 Ti computeCapability: 7.5
coreClock: 1.545GHz coreCount: 68 deviceMemorySize: 10.76GiB deviceMemoryBandwidth: 573.69GiB/s
2020-09-23 11:56:45.165445: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcudart.so.10.1
2020-09-23 11:56:45.167184: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcublas.so.10
2020-09-23 11:56:45.168816: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcufft.so.10
2020-09-23 11:56:45.169119: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcurand.so.10
2020-09-23 11:56:45.170892: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcusolv

I0923 11:56:45.903434 140453499561792 efficientnet_model.py:717] Built stem stem : (2, 448, 448, 40)
I0923 11:56:45.903612 140453499561792 efficientnet_model.py:738] block_0 survival_prob: 1.0
I0923 11:56:45.903851 140453499561792 efficientnet_model.py:372] Block blocks_0 input shape: (2, 448, 448, 40)
I0923 11:56:45.922300 140453499561792 efficientnet_model.py:391] DWConv shape: (2, 448, 448, 40)
I0923 11:56:45.937679 140453499561792 efficientnet_model.py:195] Built SE se : (2, 1, 1, 40)
I0923 11:56:45.955849 140453499561792 efficientnet_model.py:412] Project shape: (2, 448, 448, 24)
I0923 11:56:45.956080 140453499561792 efficientnet_model.py:738] block_1 survival_prob: 0.9923076923076923
I0923 11:56:45.956327 140453499561792 efficientnet_model.py:372] Block blocks_1 input shape: (2, 448, 448, 24)
I0923 11:56:45.975012 140453499561792 efficientnet_model.py:391] DWConv shape: (2, 448, 448, 24)
I0923 11:56:45.992080 140453499561792 efficientnet_model.py:195] Built SE se : (2, 1, 1, 24)


I0923 11:56:47.115436 140453499561792 efficientnet_model.py:391] DWConv shape: (2, 56, 56, 816)
I0923 11:56:47.132308 140453499561792 efficientnet_model.py:195] Built SE se : (2, 1, 1, 816)
I0923 11:56:47.155210 140453499561792 efficientnet_model.py:412] Project shape: (2, 56, 56, 136)
I0923 11:56:47.155479 140453499561792 efficientnet_model.py:738] block_15 survival_prob: 0.8846153846153847
I0923 11:56:47.155750 140453499561792 efficientnet_model.py:372] Block blocks_15 input shape: (2, 56, 56, 136)
I0923 11:56:47.174813 140453499561792 efficientnet_model.py:388] Expand shape: (2, 56, 56, 816)
I0923 11:56:47.194657 140453499561792 efficientnet_model.py:391] DWConv shape: (2, 56, 56, 816)
I0923 11:56:47.212446 140453499561792 efficientnet_model.py:195] Built SE se : (2, 1, 1, 816)
I0923 11:56:47.234936 140453499561792 efficientnet_model.py:412] Project shape: (2, 56, 56, 136)
I0923 11:56:47.235247 140453499561792 efficientnet_model.py:738] block_16 survival_prob: 0.8769230769230769
I09

Instructions for updating:
Use keras.layers.MaxPooling2D instead.
W0923 11:56:48.700316 140453499561792 deprecation.py:323] From /home/iav/code/williamhyin_automl/efficientdet/efficientdet_arch.py:112: max_pooling2d (from tensorflow.python.keras.legacy_tf_layers.pooling) is deprecated and will be removed in a future version.
Instructions for updating:
Use keras.layers.MaxPooling2D instead.
I0923 11:56:48.705337 140453499561792 efficientdet_arch.py:399] building cell 0
I0923 11:56:48.705550 140453499561792 efficientdet_arch.py:490] fnode 0 : {'feat_level': 6, 'inputs_offsets': [3, 4]}
Instructions for updating:
Use `tf.keras.layers.SeparableConv2D` instead.
W0923 11:56:48.715803 140453499561792 deprecation.py:323] From /home/iav/code/williamhyin_automl/efficientdet/efficientdet_arch.py:525: separable_conv2d (from tensorflow.python.keras.legacy_tf_layers.convolutional) is deprecated and will be removed in a future version.
Instructions for updating:
Use `tf.keras.layers.SeparableConv2D` 

...

INFO:tensorflow:Calling checkpoint listeners before saving checkpoint 185000...
I0924 04:14:01.928369 140453499561792 basic_session_run_hooks.py:614] Calling checkpoint listeners before saving checkpoint 185000...
INFO:tensorflow:Saving checkpoints for 185000 into /home/iav/code/williamhyin_automl/efficientdet/tmp/d3_dfg_subset_adam/model.ckpt.
I0924 04:14:01.928660 140453499561792 basic_session_run_hooks.py:618] Saving checkpoints for 185000 into /home/iav/code/williamhyin_automl/efficientdet/tmp/d3_dfg_subset_adam/model.ckpt.
INFO:tensorflow:Calling checkpoint listeners after saving checkpoint 185000...
I0924 04:14:07.054891 140453499561792 basic_session_run_hooks.py:626] Calling checkpoint listeners after saving checkpoint 185000...
INFO:tensorflow:global_step/sec: 2.76778
I0924 04:14:07.409069 140453499561792 basic_session_run_hooks.py:702] global_step/sec: 2.76778
INFO:tensorflow:loss = 0.22608283, step = 185000 (36.131 sec)
I0924 04:14:07.411479 140453499561792 basic_session_run_

INFO:tensorflow:global_step/sec: 2.76184
I0924 04:19:27.605126 140453499561792 basic_session_run_hooks.py:702] global_step/sec: 2.76184
INFO:tensorflow:loss = 0.21400937, step = 186000 (36.211 sec)
I0924 04:19:27.609079 140453499561792 basic_session_run_hooks.py:260] loss = 0.21400937, step = 186000 (36.211 sec)
INFO:tensorflow:box_loss = 0.00012592012, cls_loss = 0.085925505, det_loss = 0.09222151, step = 186000 (36.211 sec)
I0924 04:19:27.609411 140453499561792 basic_session_run_hooks.py:260] box_loss = 0.00012592012, cls_loss = 0.085925505, det_loss = 0.09222151, step = 186000 (36.211 sec)
INFO:tensorflow:global_step/sec: 3.22454
I0924 04:19:58.617352 140453499561792 basic_session_run_hooks.py:702] global_step/sec: 3.22454
INFO:tensorflow:loss = 0.21390253, step = 186100 (31.010 sec)
I0924 04:19:58.618618 140453499561792 basic_session_run_hooks.py:260] loss = 0.21390253, step = 186100 (31.010 sec)
INFO:tensorflow:box_loss = 0.00012846515, cls_loss = 0.08569144, det_loss = 0.09211469

INFO:tensorflow:global_step/sec: 3.22935
I0924 04:25:49.658214 140453499561792 basic_session_run_hooks.py:702] global_step/sec: 3.22935
INFO:tensorflow:loss = 0.21125194, step = 187200 (30.966 sec)
I0924 04:25:49.659642 140453499561792 basic_session_run_hooks.py:260] loss = 0.21125194, step = 187200 (30.966 sec)
INFO:tensorflow:box_loss = 8.096204e-05, cls_loss = 0.0854162, det_loss = 0.0894643, step = 187200 (30.966 sec)
I0924 04:25:49.660049 140453499561792 basic_session_run_hooks.py:260] box_loss = 8.096204e-05, cls_loss = 0.0854162, det_loss = 0.0894643, step = 187200 (30.966 sec)
INFO:tensorflow:global_step/sec: 3.23002
I0924 04:26:20.617770 140453499561792 basic_session_run_hooks.py:702] global_step/sec: 3.23002
INFO:tensorflow:loss = 0.19318834, step = 187300 (30.959 sec)
I0924 04:26:20.619106 140453499561792 basic_session_run_hooks.py:260] loss = 0.19318834, step = 187300 (30.959 sec)
INFO:tensorflow:box_loss = 6.556838e-05, cls_loss = 0.06812227, det_loss = 0.07140069, step = 

INFO:tensorflow:global_step/sec: 3.21611
I0924 04:32:11.925371 140453499561792 basic_session_run_hooks.py:702] global_step/sec: 3.21611
INFO:tensorflow:loss = 0.23863798, step = 188400 (31.094 sec)
I0924 04:32:11.926706 140453499561792 basic_session_run_hooks.py:260] loss = 0.23863798, step = 188400 (31.094 sec)
INFO:tensorflow:box_loss = 0.00018239515, cls_loss = 0.10773064, det_loss = 0.1168504, step = 188400 (31.094 sec)
I0924 04:32:11.927089 140453499561792 basic_session_run_hooks.py:260] box_loss = 0.00018239515, cls_loss = 0.10773064, det_loss = 0.1168504, step = 188400 (31.094 sec)
INFO:tensorflow:Calling checkpoint listeners before saving checkpoint 188500...
I0924 04:32:42.582731 140453499561792 basic_session_run_hooks.py:614] Calling checkpoint listeners before saving checkpoint 188500...
INFO:tensorflow:Saving checkpoints for 188500 into /home/iav/code/williamhyin_automl/efficientdet/tmp/d3_dfg_subset_adam/model.ckpt.
I0924 04:32:42.583058 140453499561792 basic_session_run_h

INFO:tensorflow:Calling checkpoint listeners after saving checkpoint 189500...
I0924 04:38:07.867416 140453499561792 basic_session_run_hooks.py:626] Calling checkpoint listeners after saving checkpoint 189500...
INFO:tensorflow:global_step/sec: 2.76677
I0924 04:38:08.224631 140453499561792 basic_session_run_hooks.py:702] global_step/sec: 2.76677
INFO:tensorflow:loss = 0.23493889, step = 189500 (36.146 sec)
I0924 04:38:08.228555 140453499561792 basic_session_run_hooks.py:260] loss = 0.23493889, step = 189500 (36.146 sec)
INFO:tensorflow:box_loss = 9.721149e-05, cls_loss = 0.10829073, det_loss = 0.113151304, step = 189500 (36.146 sec)
I0924 04:38:08.228883 140453499561792 basic_session_run_hooks.py:260] box_loss = 9.721149e-05, cls_loss = 0.10829073, det_loss = 0.113151304, step = 189500 (36.146 sec)
INFO:tensorflow:global_step/sec: 3.22852
I0924 04:38:39.198595 140453499561792 basic_session_run_hooks.py:702] global_step/sec: 3.22852
INFO:tensorflow:loss = 0.22394761, step = 189600 (30.9

In [27]:
d="d1"
times="dfg_subset_adam"
!rm -r /home/iav/code/williamhyin_automl/efficientdet/tmp/{d}_{times} 
!mkdir /home/iav/code/williamhyin_automl/efficientdet/tmp/{d}_{times} 
!python main.py --mode=train\
    --training_file_pattern=/home/iav/code/bigdata/dfg_efficientdet/train_subset_tfrecord/train* \
    --model_name=efficientdet-{d} \
    --model_dir=/home/iav/code/williamhyin_automl/efficientdet/tmp/{d}_{times}  \
    --ckpt=/home/iav/code/williamhyin_automl/efficientdet/weights/efficientdet-{d}  \
    --train_batch_size=4 \
    --num_examples_per_epoch=1269 --num_epochs=300  \
    --hparams=/home/iav/code/williamhyin_automl/efficientdet/configs/dfg_d1_adam.yaml \
    --save_checkpoints_steps=500 \

2020-09-24 09:35:36.872449: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcudart.so.10.1
I0924 09:35:38.123987 140020877899584 main.py:227] {'name': 'efficientdet-d1', 'act_type': 'swish', 'image_size': (640, 640), 'target_size': None, 'input_rand_hflip': True, 'jitter_min': 0.1, 'jitter_max': 2.0, 'autoaugment_policy': None, 'use_augmix': False, 'augmix_params': [3, -1, 1], 'sample_image': None, 'num_classes': 201, 'seg_num_classes': 3, 'heads': ['object_detection'], 'skip_crowd_during_training': True, 'label_map': {0: 'background', 1: 'I-1.1', 2: 'I-10', 3: 'I-11', 4: 'I-13', 5: 'I-13.1', 6: 'I-14', 7: 'I-15', 8: 'I-16', 9: 'I-17', 10: 'I-18', 11: 'I-19', 12: 'I-2', 13: 'I-2.1', 14: 'I-20', 15: 'I-25', 16: 'I-27', 17: 'I-28', 18: 'I-28.1', 19: 'I-29', 20: 'I-29.1', 21: 'I-3', 22: 'I-30', 23: 'I-32', 24: 'I-34', 25: 'I-36', 26: 'I-37', 27: 'I-38', 28: 'I-39-1', 29: 'I-39-2', 30: 'I-39-3', 31: 'I-4', 32: 'I-5', 33: 'I-5.1', 34: '

2020-09-24 09:35:38.171043: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcuda.so.1
2020-09-24 09:35:38.209729: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1716] Found device 0 with properties: 
pciBusID: 0000:21:00.0 name: GeForce RTX 2080 Ti computeCapability: 7.5
coreClock: 1.545GHz coreCount: 68 deviceMemorySize: 10.76GiB deviceMemoryBandwidth: 573.69GiB/s
2020-09-24 09:35:38.209769: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcudart.so.10.1
2020-09-24 09:35:38.211168: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcublas.so.10
2020-09-24 09:35:38.212567: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcufft.so.10
2020-09-24 09:35:38.212820: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcurand.so

I0924 09:35:38.910987 140020877899584 efficientnet_model.py:717] Built stem stem : (4, 320, 320, 32)
I0924 09:35:38.911162 140020877899584 efficientnet_model.py:738] block_0 survival_prob: 1.0
I0924 09:35:38.911407 140020877899584 efficientnet_model.py:372] Block blocks_0 input shape: (4, 320, 320, 32)
I0924 09:35:38.929748 140020877899584 efficientnet_model.py:391] DWConv shape: (4, 320, 320, 32)
I0924 09:35:38.944932 140020877899584 efficientnet_model.py:195] Built SE se : (4, 1, 1, 32)
I0924 09:35:38.963300 140020877899584 efficientnet_model.py:412] Project shape: (4, 320, 320, 16)
I0924 09:35:38.963539 140020877899584 efficientnet_model.py:738] block_1 survival_prob: 0.991304347826087
I0924 09:35:38.963785 140020877899584 efficientnet_model.py:372] Block blocks_1 input shape: (4, 320, 320, 16)
I0924 09:35:38.982572 140020877899584 efficientnet_model.py:391] DWConv shape: (4, 320, 320, 16)
I0924 09:35:38.997982 140020877899584 efficientnet_model.py:195] Built SE se : (4, 1, 1, 16)
I

I0924 09:35:40.030448 140020877899584 efficientnet_model.py:412] Project shape: (4, 40, 40, 112)
I0924 09:35:40.030760 140020877899584 efficientnet_model.py:738] block_14 survival_prob: 0.8782608695652174
I0924 09:35:40.031098 140020877899584 efficientnet_model.py:372] Block blocks_14 input shape: (4, 40, 40, 112)
I0924 09:35:40.050740 140020877899584 efficientnet_model.py:388] Expand shape: (4, 40, 40, 672)
I0924 09:35:40.070161 140020877899584 efficientnet_model.py:391] DWConv shape: (4, 40, 40, 672)
I0924 09:35:40.086882 140020877899584 efficientnet_model.py:195] Built SE se : (4, 1, 1, 672)
I0924 09:35:40.110914 140020877899584 efficientnet_model.py:412] Project shape: (4, 40, 40, 112)
I0924 09:35:40.111178 140020877899584 efficientnet_model.py:738] block_15 survival_prob: 0.8695652173913044
I0924 09:35:40.111444 140020877899584 efficientnet_model.py:372] Block blocks_15 input shape: (4, 40, 40, 112)
I0924 09:35:40.131516 140020877899584 efficientnet_model.py:388] Expand shape: (4,

I0924 09:35:41.343271 140020877899584 efficientdet_arch.py:399] building cell 0
I0924 09:35:41.343465 140020877899584 efficientdet_arch.py:490] fnode 0 : {'feat_level': 6, 'inputs_offsets': [3, 4]}
Instructions for updating:
Use `tf.keras.layers.SeparableConv2D` instead.
W0924 09:35:41.353582 140020877899584 deprecation.py:323] From /home/iav/code/williamhyin_automl/efficientdet/efficientdet_arch.py:525: separable_conv2d (from tensorflow.python.keras.legacy_tf_layers.convolutional) is deprecated and will be removed in a future version.
Instructions for updating:
Use `tf.keras.layers.SeparableConv2D` instead.
I0924 09:35:41.403178 140020877899584 efficientdet_arch.py:490] fnode 1 : {'feat_level': 5, 'inputs_offsets': [2, 5]}
I0924 09:35:41.502922 140020877899584 efficientdet_arch.py:490] fnode 2 : {'feat_level': 4, 'inputs_offsets': [1, 6]}
I0924 09:35:41.604125 140020877899584 efficientdet_arch.py:490] fnode 3 : {'feat_level': 3, 'inputs_offsets': [0, 7]}
I0924 09:35:41.703150 14002087

...

INFO:tensorflow:global_step/sec: 4.43092
I0924 15:27:38.016497 140020877899584 basic_session_run_hooks.py:702] global_step/sec: 4.43092
INFO:tensorflow:loss = 10.144696, step = 90400 (22.569 sec)
I0924 15:27:38.017655 140020877899584 basic_session_run_hooks.py:260] loss = 10.144696, step = 90400 (22.569 sec)
INFO:tensorflow:box_loss = 0.0004675714, cls_loss = 10.0, det_loss = 10.023378, step = 90400 (22.569 sec)
I0924 15:27:38.018014 140020877899584 basic_session_run_hooks.py:260] box_loss = 0.0004675714, cls_loss = 10.0, det_loss = 10.023378, step = 90400 (22.569 sec)
INFO:tensorflow:Calling checkpoint listeners before saving checkpoint 90500...
I0924 15:28:00.479850 140020877899584 basic_session_run_hooks.py:614] Calling checkpoint listeners before saving checkpoint 90500...
INFO:tensorflow:Saving checkpoints for 90500 into /home/iav/code/williamhyin_automl/efficientdet/tmp/d1_dfg_subset_adam/model.ckpt.
I0924 15:28:00.480133 140020877899584 basic_session_run_hooks.py:618] Saving che

INFO:tensorflow:Calling checkpoint listeners after saving checkpoint 91500...
I0924 15:31:55.918296 140020877899584 basic_session_run_hooks.py:626] Calling checkpoint listeners after saving checkpoint 91500...
INFO:tensorflow:global_step/sec: 3.88323
I0924 15:31:56.175185 140020877899584 basic_session_run_hooks.py:702] global_step/sec: 3.88323
INFO:tensorflow:loss = 10.127576, step = 91500 (25.753 sec)
I0924 15:31:56.177999 140020877899584 basic_session_run_hooks.py:260] loss = 10.127576, step = 91500 (25.753 sec)
INFO:tensorflow:box_loss = 0.00012516021, cls_loss = 10.0, det_loss = 10.006258, step = 91500 (25.753 sec)
I0924 15:31:56.178344 140020877899584 basic_session_run_hooks.py:260] box_loss = 0.00012516021, cls_loss = 10.0, det_loss = 10.006258, step = 91500 (25.753 sec)
INFO:tensorflow:global_step/sec: 4.44255
I0924 15:32:18.684750 140020877899584 basic_session_run_hooks.py:702] global_step/sec: 4.44255
INFO:tensorflow:loss = 10.178187, step = 91600 (22.508 sec)
I0924 15:32:18.6

INFO:tensorflow:global_step/sec: 4.41856
I0924 15:36:33.402040 140020877899584 basic_session_run_hooks.py:702] global_step/sec: 4.41856
INFO:tensorflow:loss = 10.163035, step = 92700 (22.632 sec)
I0924 15:36:33.403274 140020877899584 basic_session_run_hooks.py:260] loss = 10.163035, step = 92700 (22.632 sec)
INFO:tensorflow:box_loss = 0.0008343586, cls_loss = 10.0, det_loss = 10.041718, step = 92700 (22.632 sec)
I0924 15:36:33.403646 140020877899584 basic_session_run_hooks.py:260] box_loss = 0.0008343586, cls_loss = 10.0, det_loss = 10.041718, step = 92700 (22.632 sec)
INFO:tensorflow:global_step/sec: 4.40829
I0924 15:36:56.086591 140020877899584 basic_session_run_hooks.py:702] global_step/sec: 4.40829
INFO:tensorflow:loss = 10.129885, step = 92800 (22.684 sec)
I0924 15:36:56.087675 140020877899584 basic_session_run_hooks.py:260] loss = 10.129885, step = 92800 (22.684 sec)
INFO:tensorflow:box_loss = 0.00017134452, cls_loss = 10.0, det_loss = 10.008567, step = 92800 (22.684 sec)
I0924 1

INFO:tensorflow:global_step/sec: 4.42929
I0924 15:41:10.877541 140020877899584 basic_session_run_hooks.py:702] global_step/sec: 4.42929
INFO:tensorflow:loss = 10.136815, step = 93900 (22.577 sec)
I0924 15:41:10.878974 140020877899584 basic_session_run_hooks.py:260] loss = 10.136815, step = 93900 (22.577 sec)
INFO:tensorflow:box_loss = 0.0003099496, cls_loss = 10.0, det_loss = 10.015497, step = 93900 (22.577 sec)
I0924 15:41:10.879406 140020877899584 basic_session_run_hooks.py:260] box_loss = 0.0003099496, cls_loss = 10.0, det_loss = 10.015497, step = 93900 (22.577 sec)
INFO:tensorflow:Calling checkpoint listeners before saving checkpoint 94000...
I0924 15:41:33.310100 140020877899584 basic_session_run_hooks.py:614] Calling checkpoint listeners before saving checkpoint 94000...
INFO:tensorflow:Saving checkpoints for 94000 into /home/iav/code/williamhyin_automl/efficientdet/tmp/d1_dfg_subset_adam/model.ckpt.
I0924 15:41:33.310251 140020877899584 basic_session_run_hooks.py:618] Saving che

INFO:tensorflow:Calling checkpoint listeners after saving checkpoint 95000...
I0924 15:45:28.612687 140020877899584 basic_session_run_hooks.py:626] Calling checkpoint listeners after saving checkpoint 95000...
INFO:tensorflow:global_step/sec: 3.884
I0924 15:45:28.868289 140020877899584 basic_session_run_hooks.py:702] global_step/sec: 3.884
INFO:tensorflow:loss = 10.145231, step = 95000 (25.749 sec)
I0924 15:45:28.871321 140020877899584 basic_session_run_hooks.py:260] loss = 10.145231, step = 95000 (25.749 sec)
INFO:tensorflow:box_loss = 0.00047826275, cls_loss = 10.0, det_loss = 10.023913, step = 95000 (25.749 sec)
I0924 15:45:28.871731 140020877899584 basic_session_run_hooks.py:260] box_loss = 0.00047826275, cls_loss = 10.0, det_loss = 10.023913, step = 95000 (25.749 sec)
INFO:tensorflow:global_step/sec: 4.42614
I0924 15:45:51.461313 140020877899584 basic_session_run_hooks.py:702] global_step/sec: 4.42614
INFO:tensorflow:loss = 10.152234, step = 95100 (22.591 sec)
I0924 15:45:51.46253

In [28]:
d="d3"
times="dfg_subset_adam"

!python main.py --mode=eval  \
--model_name=efficientdet-{d} \
--model_dir=/home/iav/code/williamhyin_automl/efficientdet/tmp/{d}_{times}   \
--validation_file_pattern=/home/iav/code/bigdata/dfg_efficientdet/test_tfrecord/test*  \
--val_json_file=/home/iav/code/trafficsign/dfg/labels/test.json \
--hparams=/home/iav/code/williamhyin_automl/efficientdet/configs/dfg_d3_adam.yaml \
--train_batch_size=2 \
--eval_batch_size=1 --eval_samples=1703 \

2020-09-25 08:50:38.386196: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcudart.so.10.1
I0925 08:50:39.710347 140131057780544 main.py:227] {'name': 'efficientdet-d3', 'act_type': 'swish', 'image_size': (896, 896), 'target_size': None, 'input_rand_hflip': True, 'jitter_min': 0.1, 'jitter_max': 2.0, 'autoaugment_policy': None, 'use_augmix': False, 'augmix_params': [3, -1, 1], 'sample_image': None, 'num_classes': 201, 'seg_num_classes': 3, 'heads': ['object_detection'], 'skip_crowd_during_training': True, 'label_map': {0: 'background', 1: 'I-1.1', 2: 'I-10', 3: 'I-11', 4: 'I-13', 5: 'I-13.1', 6: 'I-14', 7: 'I-15', 8: 'I-16', 9: 'I-17', 10: 'I-18', 11: 'I-19', 12: 'I-2', 13: 'I-2.1', 14: 'I-20', 15: 'I-25', 16: 'I-27', 17: 'I-28', 18: 'I-28.1', 19: 'I-29', 20: 'I-29.1', 21: 'I-3', 22: 'I-30', 23: 'I-32', 24: 'I-34', 25: 'I-36', 26: 'I-37', 27: 'I-38', 28: 'I-39-1', 29: 'I-39-2', 30: 'I-39-3', 31: 'I-4', 32: 'I-5', 33: 'I-5.1', 34: '

2020-09-25 08:50:39.870186: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcuda.so.1
2020-09-25 08:50:39.904943: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1716] Found device 0 with properties: 
pciBusID: 0000:21:00.0 name: GeForce RTX 2080 Ti computeCapability: 7.5
coreClock: 1.545GHz coreCount: 68 deviceMemorySize: 10.76GiB deviceMemoryBandwidth: 573.69GiB/s
2020-09-25 08:50:39.904981: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcudart.so.10.1
2020-09-25 08:50:39.906210: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcublas.so.10
2020-09-25 08:50:39.907449: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcufft.so.10
2020-09-25 08:50:39.907732: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcurand.so

I0925 08:50:40.480858 140131057780544 efficientnet_model.py:717] Built stem stem : (1, 448, 448, 40)
I0925 08:50:40.481034 140131057780544 efficientnet_model.py:738] block_0 survival_prob: 1.0
I0925 08:50:40.481265 140131057780544 efficientnet_model.py:372] Block blocks_0 input shape: (1, 448, 448, 40)
I0925 08:50:40.495251 140131057780544 efficientnet_model.py:391] DWConv shape: (1, 448, 448, 40)
I0925 08:50:40.510044 140131057780544 efficientnet_model.py:195] Built SE se : (1, 1, 1, 40)
I0925 08:50:40.523164 140131057780544 efficientnet_model.py:412] Project shape: (1, 448, 448, 24)
I0925 08:50:40.523343 140131057780544 efficientnet_model.py:738] block_1 survival_prob: 0.9923076923076923
I0925 08:50:40.523564 140131057780544 efficientnet_model.py:372] Block blocks_1 input shape: (1, 448, 448, 24)
I0925 08:50:40.537468 140131057780544 efficientnet_model.py:391] DWConv shape: (1, 448, 448, 24)
I0925 08:50:40.552562 140131057780544 efficientnet_model.py:195] Built SE se : (1, 1, 1, 24)


I0925 08:50:41.353469 140131057780544 efficientnet_model.py:388] Expand shape: (1, 56, 56, 816)
I0925 08:50:41.368320 140131057780544 efficientnet_model.py:391] DWConv shape: (1, 56, 56, 816)
I0925 08:50:41.384116 140131057780544 efficientnet_model.py:195] Built SE se : (1, 1, 1, 816)
I0925 08:50:41.397723 140131057780544 efficientnet_model.py:412] Project shape: (1, 56, 56, 136)
I0925 08:50:41.397945 140131057780544 efficientnet_model.py:738] block_15 survival_prob: 0.8846153846153847
I0925 08:50:41.398213 140131057780544 efficientnet_model.py:372] Block blocks_15 input shape: (1, 56, 56, 136)
I0925 08:50:41.412546 140131057780544 efficientnet_model.py:388] Expand shape: (1, 56, 56, 816)
I0925 08:50:41.427700 140131057780544 efficientnet_model.py:391] DWConv shape: (1, 56, 56, 816)
I0925 08:50:41.443197 140131057780544 efficientnet_model.py:195] Built SE se : (1, 1, 1, 816)
I0925 08:50:41.456540 140131057780544 efficientnet_model.py:412] Project shape: (1, 56, 56, 136)
I0925 08:50:41.

Instructions for updating:
Use keras.layers.MaxPooling2D instead.
W0925 08:50:42.490964 140131057780544 deprecation.py:323] From /home/iav/code/williamhyin_automl/efficientdet/efficientdet_arch.py:112: max_pooling2d (from tensorflow.python.keras.legacy_tf_layers.pooling) is deprecated and will be removed in a future version.
Instructions for updating:
Use keras.layers.MaxPooling2D instead.
I0925 08:50:42.495954 140131057780544 efficientdet_arch.py:399] building cell 0
I0925 08:50:42.496168 140131057780544 efficientdet_arch.py:490] fnode 0 : {'feat_level': 6, 'inputs_offsets': [3, 4]}
Instructions for updating:
Use `tf.keras.layers.SeparableConv2D` instead.
W0925 08:50:42.505879 140131057780544 deprecation.py:323] From /home/iav/code/williamhyin_automl/efficientdet/efficientdet_arch.py:525: separable_conv2d (from tensorflow.python.keras.legacy_tf_layers.convolutional) is deprecated and will be removed in a future version.
Instructions for updating:
Use `tf.keras.layers.SeparableConv2D` 

INFO:tensorflow:Done calling model_fn.
I0925 08:50:52.230736 140131057780544 estimator.py:1164] Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2020-09-25T08:50:52Z
I0925 08:50:52.241954 140131057780544 evaluation.py:255] Starting evaluation at 2020-09-25T08:50:52Z
INFO:tensorflow:Graph was finalized.
I0925 08:50:52.588222 140131057780544 monitored_session.py:246] Graph was finalized.
2020-09-25 08:50:52.588477: I tensorflow/core/platform/cpu_feature_guard.cc:142] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN)to use the following CPU instructions in performance-critical operations:  AVX2 AVX512F FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2020-09-25 08:50:52.611223: I tensorflow/core/platform/profile_utils/cpu_utils.cc:104] CPU Frequency: 3699850000 Hz
2020-09-25 08:50:52.612201: I tensorflow/compiler/xla/service/service.cc:168] XLA service 0x55fb13ecaa80 initialized for platform Hos

INFO:tensorflow:Saving 'checkpoint_path' summary for global step 190350: /home/iav/code/williamhyin_automl/efficientdet/tmp/d3_dfg_subset_adam/model.ckpt-190350
I0925 09:00:57.098263 140131057780544 estimator.py:2124] Saving 'checkpoint_path' summary for global step 190350: /home/iav/code/williamhyin_automl/efficientdet/tmp/d3_dfg_subset_adam/model.ckpt-190350
INFO:tensorflow:/home/iav/code/williamhyin_automl/efficientdet/tmp/d3_dfg_subset_adam/archive/model.ckpt-190350 is not in all_model_checkpoint_paths. Manually adding it.
I0925 09:00:57.220560 140131057780544 checkpoint_management.py:102] /home/iav/code/williamhyin_automl/efficientdet/tmp/d3_dfg_subset_adam/archive/model.ckpt-190350 is not in all_model_checkpoint_paths. Manually adding it.
I0925 09:00:57.221109 140131057780544 utils.py:514] Copying checkpoint /home/iav/code/williamhyin_automl/efficientdet/tmp/d3_dfg_subset_adam/model.ckpt-190350 to /home/iav/code/williamhyin_automl/efficientdet/tmp/d3_dfg_subset_adam/archive
INFO:

In [29]:
d="d3"
times="dfg_subset_adam"
!rm  -rf /home/iav/code/williamhyin_automl/efficientdet/tmp/{d}_{times}/finetune{d}_{times}_export
!python model_inspect.py --runmode=saved_model --model_name=efficientdet-{d} \
  --ckpt_path=/home/iav/code/williamhyin_automl/efficientdet/tmp/{d}_{times}  \
  --saved_model_dir=/home/iav/code/williamhyin_automl/efficientdet/tmp/{d}_{times}/finetune{d}_{times}_export \
  --hparams=/home/iav/code/williamhyin_automl/efficientdet/configs/dfg_d3_adam.yaml


2020-09-25 09:05:44.532533: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcudart.so.10.1
2020-09-25 09:05:45.871365: I tensorflow/core/platform/cpu_feature_guard.cc:142] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN)to use the following CPU instructions in performance-critical operations:  AVX2 AVX512F FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2020-09-25 09:05:45.895198: I tensorflow/core/platform/profile_utils/cpu_utils.cc:104] CPU Frequency: 3699850000 Hz
2020-09-25 09:05:45.896349: I tensorflow/compiler/xla/service/service.cc:168] XLA service 0x55d240c3d230 initialized for platform Host (this does not guarantee that XLA will be used). Devices:
2020-09-25 09:05:45.896393: I tensorflow/compiler/xla/service/service.cc:176]   StreamExecutor device (0): Host, Default Version
2020-09-25 09:05:45.901063: I tensorflow/stream_executor/platform/d

3 ops no flops stats due to incomplete shapes.
Incomplete shape.
Incomplete shape.
3 ops no flops stats due to incomplete shapes.
Incomplete shape.
Incomplete shape.
Instructions for updating:
Use Variable.read_value. Variables in 2.X are initialized automatically both in eager and graph (inside tf.defun) contexts.
W0925 09:06:00.942650 139945105762112 deprecation.py:323] From /home/iav/anaconda3/envs/tf2/lib/python3.6/site-packages/tensorflow/python/training/moving_averages.py:458: Variable.initialized_value (from tensorflow.python.ops.variables) is deprecated and will be removed in a future version.
Instructions for updating:
Use Variable.read_value. Variables in 2.X are initialized automatically both in eager and graph (inside tf.defun) contexts.
Instructions for updating:
This function will only be available through the v1 compatibility library as tf.compat.v1.saved_model.utils.build_tensor_info or tf.compat.v1.saved_model.build_tensor_info.
W0925 09:06:23.173741 139945105762112 de

In [30]:
!mkdir /home/iav/code/trafficsign/dfg/inference
!python model_inspect.py --runmode=saved_model_infer \
  --model_name=efficientdet-{d}  \
  --saved_model_dir=/home/iav/code/williamhyin_automl/efficientdet/tmp/{d}_{times}/finetune{d}_{times}_export \
  --input_image=/home/iav/code/trafficsign/dfg/images/test/*.jpg\
  --output_image_dir=/home/iav/code/trafficsign/dfg/inference \
  --hparams=/home/iav/code/williamhyin_automl/efficientdet/configs/dfg_d3_adam.yaml \
  --min_score_thresh=0.3
  

mkdir: 无法创建目录"/home/iav/code/trafficsign/dfg/inference": 文件已存在
2020-09-25 09:11:33.136204: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcudart.so.10.1
2020-09-25 09:11:34.430211: I tensorflow/core/platform/cpu_feature_guard.cc:142] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN)to use the following CPU instructions in performance-critical operations:  AVX2 AVX512F FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2020-09-25 09:11:34.455032: I tensorflow/core/platform/profile_utils/cpu_utils.cc:104] CPU Frequency: 3699850000 Hz
2020-09-25 09:11:34.456102: I tensorflow/compiler/xla/service/service.cc:168] XLA service 0x55ff6871afb0 initialized for platform Host (this does not guarantee that XLA will be used). Devices:
2020-09-25 09:11:34.456147: I tensorflow/compiler/xla/service/service.cc:176]   StreamExecutor device (0): Host, Default Version
2020

2020-09-25 09:11:45.449922: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcudnn.so.7
2020-09-25 09:11:46.410467: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcublas.so.10
writing file to /home/iav/code/trafficsign/dfg/inference/0.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/2.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/3.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/4.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/5.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/6.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/7.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/8.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/9.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/10.jpg
writing file to /hom

writing file to /home/iav/code/trafficsign/dfg/inference/124.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/125.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/126.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/127.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/128.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/129.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/130.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/131.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/132.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/133.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/134.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/135.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/136.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/137.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/138.jpg
writing file to /home/iav

writing file to /home/iav/code/trafficsign/dfg/inference/251.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/252.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/253.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/254.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/255.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/256.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/257.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/258.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/259.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/260.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/261.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/262.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/263.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/264.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/265.jpg
writing file to /home/iav

writing file to /home/iav/code/trafficsign/dfg/inference/378.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/379.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/380.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/381.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/382.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/383.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/384.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/385.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/386.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/387.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/388.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/389.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/390.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/391.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/392.jpg
writing file to /home/iav

...

writing file to /home/iav/code/trafficsign/dfg/inference/1137.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1138.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1139.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1140.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1141.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1142.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1143.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1144.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1145.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1146.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1147.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1148.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1149.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1150.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1151.jpg
writing fi

writing file to /home/iav/code/trafficsign/dfg/inference/1262.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1263.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1264.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1265.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1266.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1267.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1268.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1269.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1270.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1271.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1272.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1273.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1274.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1275.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1276.jpg
writing fi

writing file to /home/iav/code/trafficsign/dfg/inference/1387.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1388.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1389.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1390.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1391.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1392.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1393.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1394.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1395.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1396.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1397.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1398.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1399.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1400.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1401.jpg
writing fi

writing file to /home/iav/code/trafficsign/dfg/inference/1512.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1513.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1514.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1515.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1516.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1517.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1518.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1519.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1520.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1521.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1522.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1523.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1524.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1525.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1526.jpg
writing fi

writing file to /home/iav/code/trafficsign/dfg/inference/1637.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1638.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1639.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1640.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1641.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1642.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1643.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1644.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1645.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1646.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1647.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1648.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1649.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1650.jpg
writing file to /home/iav/code/trafficsign/dfg/inference/1651.jpg
writing fi

In [34]:
d="d3"
b="b3"
times="dfg_subset_adam"
!rm -r /home/iav/code/williamhyin_automl/efficientdet/tmp/{b}_{times} 
!mkdir /home/iav/code/williamhyin_automl/efficientdet/tmp/{b}_{times} 
!python main.py --mode=train\
    --training_file_pattern=/home/iav/code/bigdata/dfg_efficientdet/train_subset_tfrecord/train* \
    --model_name=efficientdet-{d} \
    --model_dir=/home/iav/code/williamhyin_automl/efficientdet/tmp/{b}_{times}  \
    --backbone_ckpt=/home/iav/code/williamhyin_automl/efficientdet/weights/efficientnet-{b}  \
    --train_batch_size=2 \
    --num_examples_per_epoch=1269 --num_epochs=300  \
    --hparams=/home/iav/code/williamhyin_automl/efficientdet/configs/dfg_d3_adam.yaml \
    --save_checkpoints_steps=500 \

2020-09-25 10:44:05.620496: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcudart.so.10.1
I0925 10:44:06.870554 140583402821440 main.py:227] {'name': 'efficientdet-d3', 'act_type': 'swish', 'image_size': (896, 896), 'target_size': None, 'input_rand_hflip': True, 'jitter_min': 0.1, 'jitter_max': 2.0, 'autoaugment_policy': None, 'use_augmix': False, 'augmix_params': [3, -1, 1], 'sample_image': None, 'num_classes': 201, 'seg_num_classes': 3, 'heads': ['object_detection'], 'skip_crowd_during_training': True, 'label_map': {0: 'background', 1: 'I-1.1', 2: 'I-10', 3: 'I-11', 4: 'I-13', 5: 'I-13.1', 6: 'I-14', 7: 'I-15', 8: 'I-16', 9: 'I-17', 10: 'I-18', 11: 'I-19', 12: 'I-2', 13: 'I-2.1', 14: 'I-20', 15: 'I-25', 16: 'I-27', 17: 'I-28', 18: 'I-28.1', 19: 'I-29', 20: 'I-29.1', 21: 'I-3', 22: 'I-30', 23: 'I-32', 24: 'I-34', 25: 'I-36', 26: 'I-37', 27: 'I-38', 28: 'I-39-1', 29: 'I-39-2', 30: 'I-39-3', 31: 'I-4', 32: 'I-5', 33: 'I-5.1', 34: '

Instructions for updating:
Use Variable.read_value. Variables in 2.X are initialized automatically both in eager and graph (inside tf.defun) contexts.
W0925 10:44:06.912207 140583402821440 deprecation.py:323] From /home/iav/anaconda3/envs/tf2/lib/python3.6/site-packages/tensorflow/python/training/training_util.py:236: Variable.initialized_value (from tensorflow.python.ops.variables) is deprecated and will be removed in a future version.
Instructions for updating:
Use Variable.read_value. Variables in 2.X are initialized automatically both in eager and graph (inside tf.defun) contexts.
2020-09-25 10:44:06.917741: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcuda.so.1
2020-09-25 10:44:06.955357: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1716] Found device 0 with properties: 
pciBusID: 0000:21:00.0 name: GeForce RTX 2080 Ti computeCapability: 7.5
coreClock: 1.545GHz coreCount: 68 deviceMemorySize: 10.76GiB deviceMemoryBand

I0925 10:44:07.679959 140583402821440 efficientnet_model.py:717] Built stem stem : (2, 448, 448, 40)
I0925 10:44:07.680160 140583402821440 efficientnet_model.py:738] block_0 survival_prob: 1.0
I0925 10:44:07.680437 140583402821440 efficientnet_model.py:372] Block blocks_0 input shape: (2, 448, 448, 40)
I0925 10:44:07.699668 140583402821440 efficientnet_model.py:391] DWConv shape: (2, 448, 448, 40)
I0925 10:44:07.715771 140583402821440 efficientnet_model.py:195] Built SE se : (2, 1, 1, 40)
I0925 10:44:07.735026 140583402821440 efficientnet_model.py:412] Project shape: (2, 448, 448, 24)
I0925 10:44:07.735296 140583402821440 efficientnet_model.py:738] block_1 survival_prob: 0.9923076923076923
I0925 10:44:07.735594 140583402821440 efficientnet_model.py:372] Block blocks_1 input shape: (2, 448, 448, 24)
I0925 10:44:07.755635 140583402821440 efficientnet_model.py:391] DWConv shape: (2, 448, 448, 24)
I0925 10:44:07.771389 140583402821440 efficientnet_model.py:195] Built SE se : (2, 1, 1, 24)


I0925 10:44:08.818479 140583402821440 efficientnet_model.py:391] DWConv shape: (2, 56, 56, 816)
I0925 10:44:08.836301 140583402821440 efficientnet_model.py:195] Built SE se : (2, 1, 1, 816)
I0925 10:44:08.860446 140583402821440 efficientnet_model.py:412] Project shape: (2, 56, 56, 136)
I0925 10:44:08.860795 140583402821440 efficientnet_model.py:738] block_15 survival_prob: 0.8846153846153847
I0925 10:44:08.861196 140583402821440 efficientnet_model.py:372] Block blocks_15 input shape: (2, 56, 56, 136)
I0925 10:44:08.881523 140583402821440 efficientnet_model.py:388] Expand shape: (2, 56, 56, 816)
I0925 10:44:08.901847 140583402821440 efficientnet_model.py:391] DWConv shape: (2, 56, 56, 816)
I0925 10:44:08.919155 140583402821440 efficientnet_model.py:195] Built SE se : (2, 1, 1, 816)
I0925 10:44:08.942382 140583402821440 efficientnet_model.py:412] Project shape: (2, 56, 56, 136)
I0925 10:44:08.942688 140583402821440 efficientnet_model.py:738] block_16 survival_prob: 0.8769230769230769
I09

Instructions for updating:
Use keras.layers.MaxPooling2D instead.
W0925 10:44:10.422142 140583402821440 deprecation.py:323] From /home/iav/code/williamhyin_automl/efficientdet/efficientdet_arch.py:112: max_pooling2d (from tensorflow.python.keras.legacy_tf_layers.pooling) is deprecated and will be removed in a future version.
Instructions for updating:
Use keras.layers.MaxPooling2D instead.
I0925 10:44:10.427190 140583402821440 efficientdet_arch.py:399] building cell 0
I0925 10:44:10.427385 140583402821440 efficientdet_arch.py:490] fnode 0 : {'feat_level': 6, 'inputs_offsets': [3, 4]}
Instructions for updating:
Use `tf.keras.layers.SeparableConv2D` instead.
W0925 10:44:10.437196 140583402821440 deprecation.py:323] From /home/iav/code/williamhyin_automl/efficientdet/efficientdet_arch.py:525: separable_conv2d (from tensorflow.python.keras.legacy_tf_layers.convolutional) is deprecated and will be removed in a future version.
Instructions for updating:
Use `tf.keras.layers.SeparableConv2D` 

...

INFO:tensorflow:global_step/sec: 3.36219
I0926 02:38:49.475549 140583402821440 basic_session_run_hooks.py:702] global_step/sec: 3.36219
INFO:tensorflow:loss = 0.9293047, step = 185300 (29.742 sec)
I0926 02:38:49.476687 140583402821440 basic_session_run_hooks.py:260] loss = 0.9293047, step = 185300 (29.742 sec)
INFO:tensorflow:box_loss = 0.00018815088, cls_loss = 0.31137222, det_loss = 0.32077977, step = 185300 (29.742 sec)
I0926 02:38:49.477043 140583402821440 basic_session_run_hooks.py:260] box_loss = 0.00018815088, cls_loss = 0.31137222, det_loss = 0.32077977, step = 185300 (29.742 sec)
INFO:tensorflow:global_step/sec: 3.35873
I0926 02:39:19.248697 140583402821440 basic_session_run_hooks.py:702] global_step/sec: 3.35873
INFO:tensorflow:loss = 1.1476011, step = 185400 (29.773 sec)
I0926 02:39:19.250032 140583402821440 basic_session_run_hooks.py:260] loss = 1.1476011, step = 185400 (29.773 sec)
INFO:tensorflow:box_loss = 0.0003039044, cls_loss = 0.5238812, det_loss = 0.53907645, step =

INFO:tensorflow:Calling checkpoint listeners before saving checkpoint 186500...
I0926 02:44:55.919335 140583402821440 basic_session_run_hooks.py:614] Calling checkpoint listeners before saving checkpoint 186500...
INFO:tensorflow:Saving checkpoints for 186500 into /home/iav/code/williamhyin_automl/efficientdet/tmp/b3_dfg_subset_adam/model.ckpt.
I0926 02:44:55.919611 140583402821440 basic_session_run_hooks.py:618] Saving checkpoints for 186500 into /home/iav/code/williamhyin_automl/efficientdet/tmp/b3_dfg_subset_adam/model.ckpt.
INFO:tensorflow:Calling checkpoint listeners after saving checkpoint 186500...
I0926 02:45:00.890593 140583402821440 basic_session_run_hooks.py:626] Calling checkpoint listeners after saving checkpoint 186500...
INFO:tensorflow:global_step/sec: 2.87823
I0926 02:45:01.240875 140583402821440 basic_session_run_hooks.py:702] global_step/sec: 2.87823
INFO:tensorflow:loss = 1.096946, step = 186500 (34.747 sec)
I0926 02:45:01.245480 140583402821440 basic_session_run_ho

INFO:tensorflow:global_step/sec: 3.36765
I0926 02:50:37.813590 140583402821440 basic_session_run_hooks.py:702] global_step/sec: 3.36765
INFO:tensorflow:loss = 1.0611385, step = 187600 (29.692 sec)
I0926 02:50:37.814713 140583402821440 basic_session_run_hooks.py:260] loss = 1.0611385, step = 187600 (29.692 sec)
INFO:tensorflow:box_loss = 0.00015567392, cls_loss = 0.44483164, det_loss = 0.45261532, step = 187600 (29.693 sec)
I0926 02:50:37.815083 140583402821440 basic_session_run_hooks.py:260] box_loss = 0.00015567392, cls_loss = 0.44483164, det_loss = 0.45261532, step = 187600 (29.693 sec)
INFO:tensorflow:global_step/sec: 3.35351
I0926 02:51:07.633107 140583402821440 basic_session_run_hooks.py:702] global_step/sec: 3.35351
INFO:tensorflow:loss = 1.1632328, step = 187700 (29.820 sec)
I0926 02:51:07.634221 140583402821440 basic_session_run_hooks.py:260] loss = 1.1632328, step = 187700 (29.820 sec)
INFO:tensorflow:box_loss = 0.00085118326, cls_loss = 0.51215047, det_loss = 0.5547096, step 

INFO:tensorflow:global_step/sec: 3.36523
I0926 02:56:44.646872 140583402821440 basic_session_run_hooks.py:702] global_step/sec: 3.36523
INFO:tensorflow:loss = 0.928597, step = 188800 (29.716 sec)
I0926 02:56:44.647970 140583402821440 basic_session_run_hooks.py:260] loss = 0.928597, step = 188800 (29.716 sec)
INFO:tensorflow:box_loss = 0.0005017712, cls_loss = 0.2949853, det_loss = 0.32007384, step = 188800 (29.716 sec)
I0926 02:56:44.648330 140583402821440 basic_session_run_hooks.py:260] box_loss = 0.0005017712, cls_loss = 0.2949853, det_loss = 0.32007384, step = 188800 (29.716 sec)
INFO:tensorflow:global_step/sec: 3.3632
I0926 02:57:14.380387 140583402821440 basic_session_run_hooks.py:702] global_step/sec: 3.3632
INFO:tensorflow:loss = 1.070318, step = 188900 (29.733 sec)
I0926 02:57:14.381116 140583402821440 basic_session_run_hooks.py:260] loss = 1.070318, step = 188900 (29.733 sec)
INFO:tensorflow:box_loss = 0.0006066707, cls_loss = 0.4314613, det_loss = 0.46179485, step = 188900 (2

INFO:tensorflow:Calling checkpoint listeners before saving checkpoint 190000...
I0926 03:02:50.961201 140583402821440 basic_session_run_hooks.py:614] Calling checkpoint listeners before saving checkpoint 190000...
INFO:tensorflow:Saving checkpoints for 190000 into /home/iav/code/williamhyin_automl/efficientdet/tmp/b3_dfg_subset_adam/model.ckpt.
I0926 03:02:50.961475 140583402821440 basic_session_run_hooks.py:618] Saving checkpoints for 190000 into /home/iav/code/williamhyin_automl/efficientdet/tmp/b3_dfg_subset_adam/model.ckpt.
INFO:tensorflow:Calling checkpoint listeners after saving checkpoint 190000...
I0926 03:02:55.856103 140583402821440 basic_session_run_hooks.py:626] Calling checkpoint listeners after saving checkpoint 190000...
INFO:tensorflow:global_step/sec: 2.87264
I0926 03:02:56.211358 140583402821440 basic_session_run_hooks.py:702] global_step/sec: 2.87264
INFO:tensorflow:loss = 1.3235741, step = 190000 (34.815 sec)
I0926 03:02:56.215987 140583402821440 basic_session_run_h

In [ ]:
# Define the classes (out of the 81) which you want to see. Others will not be shown.
filterClasses = ['II-6']

# Fetch class IDs only corresponding to the filterClasses
catIds = coco.getCatIds(catNms=filterClasses) 
# Get all images containing the above Category IDs
imgIds = coco.getImgIds(catIds=catIds)
print("Number of images containing all the  classes:", len(imgIds))
print("Names of images containing all the  classes:",imgIds)
# load and display a random image
img = coco.loadImgs(imgIds[np.random.randint(0,len(imgIds))])[0]
I = io.imread('{}{}'.format(imgs_path,img['file_name']))/255.0

plt.axis('off')
plt.imshow(I)
plt.show()

In [ ]:
plt.imshow(I)
plt.axis('off')
annIds = coco.getAnnIds(imgIds=img['id'], catIds=catIds, iscrowd=None)
anns = coco.loadAnns(annIds)
coco.showAnns(anns)

In [ ]:

########## ALl POSSIBLE COMBINATIONS ########
classes = catNAMEs

images = []
if classes!=None:
    # iterate for each individual class in the list
    for className in classes:
        # get all images containing given class
        catIds = coco.getCatIds(catNms=className)
        imgIds = coco.getImgIds(catIds=catIds)
        images += coco.loadImgs(imgIds)
else:
    imgIds = coco.getImgIds()
    images = coco.loadImgs(imgIds)
    
# Now, filter out the repeated images    
unique_images = []
for i in range(len(images)):
    if images[i] not in unique_images:
        unique_images.append(images[i])

dataset_size = len(unique_images)

print("Number of images containing the filter classes:", dataset_size)
print("Number of repeated images containing the filter classes:", len(images))

In [ ]:
filterClasses = catNAMEs
mask = np.zeros((img['height'],img['width']))
for i in range(len(anns)):
    className = getClassName(anns[i]['category_id'], cats)
    pixel_value = filterClasses.index(className)+1
    mask = np.maximum(coco.annToMask(anns[i])*pixel_value, mask)
plt.imshow(mask)

In [ ]:

#### GENERATE A BINARY MASK ####
mask = np.zeros((img['height'],img['width']))
for i in range(len(anns)):
    mask = np.maximum(coco.annToMask(anns[i]), mask)
plt.imshow(mask)

In [ ]:
from pycocotools.coco import COCO
import numpy as np
import skimage.io as io
import random
import os
import cv2
### For visualizing the outputs ###
import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec
%matplotlib inline
base_path="../trafficsign/"
imgs_path="../trafficsign/JPEGImages/"
difficult_labels=base_path+"DFG-tsd-aug-annot-json-with-difficult-samples/train-difficult.json"
aug_lables=base_path+"DFG-tsd-aug-annot-json/train.json"
test_labels=base_path+"DFG-tsd-aug-annot-json/test.json"
catagory_path=base_path+"DFG-tsd-category-info/"
from pycocotools.coco import COCO
import skimage.io as io
import matplotlib.pyplot as plt
import pylab, os, cv2, shutil
import os.path as osp
import numpy as np
import glob
import random

coco_classes=['I-1','I-1.1','I-10','I-11','I-13','I-13.1','I-14','I-15','I-16','I-17','I-18','I-19','I-2','I-2.1','I-20','I-25','I-27','I-28','I-28.1','I-29','I-29.1','I-3','I-30','I-32','I-34','I-36','I-37','I-38','I-39-1','I-39-2','I-39-3','I-4','I-5','I-5.1','I-5.2','I-8','I-9','II-1','II-10.1','II-14','II-17','II-18','II-19-4','II-2','II-21','II-22','II-23','II-26','II-26.1','II-28','II-3','II-30-10','II-30-30','II-30-40','II-30-50','II-30-60','II-30-70','II-32','II-33','II-34','II-35','II-39','II-4','II-40','II-41','II-42','II-42.1','II-43','II-45','II-45.1','II-45.2','II-46','II-46.1','II-46.2','II-47','II-47.1','II-48','II-6','II-7','II-7.1','II-8','III-1','III-10','III-105','III-105.1','III-105.3','III-107-1','III-107-2','III-107.1-1','III-107.1-2','III-107.2-1','III-107.2-2','III-112','III-113','III-12','III-120','III-120-1','III-120.1','III-123','III-124','III-14','III-14.1','III-15','III-16','III-18-40','III-18-50','III-18-60','III-18-70','III-2','III-202-5','III-203-2','III-206-1','III-21','III-23','III-25','III-25.1','III-27','III-29-30','III-29-40','III-3','III-30-30','III-33','III-34','III-35','III-37','III-39','III-40','III-42','III-43','III-45','III-46','III-47','III-5','III-50','III-54','III-59','III-6','III-64','III-68','III-74','III-77','III-78','III-8-1','III-84','III-84-1','III-85-2','III-85-3','III-85.1','III-86-1','III-86-2','III-87','III-90','III-90.1','III-90.2','III-91','IV-1','IV-1.1','IV-10','IV-11','IV-12','IV-12.1','IV-13-1','IV-13-2','IV-13-3','IV-13-4','IV-13-5','IV-13-6','IV-13.1-2','IV-13.1-3','IV-13.1-4','IV-16','IV-17','IV-18','IV-2','IV-20-1','IV-3-1','IV-3-2','IV-3-4','IV-3-5','IV-5','IV-6','VI-2.1','VI-3-1','VI-3-2','VI-3.1-1','VI-3.1-2','VI-8','VII-4','VII-4-1','VII-4-2','VII-4.1-1','VII-4.3','VII-4.3-1','VII-4.3-2','VII-4.4-1','VII-4.4-2','X-1.1','X-1.2','X-4','X-6-3']

SelectedCats=coco_classes

def showimg(coco, img_prefix, img, SelectedCats=None):
    I= cv2.imread(os.path.join(img_prefix,img['file_name']))
    plt.imshow(I)
    plt.axis('off')
    annIds = coco.getAnnIds(imgIds=img['id'], iscrowd=None)
    anns = coco.loadAnns(annIds)
    coco.showAnns(anns)
    plt.show()

def showbyplt(coco, img_prefix, img, classes, SelectedCats=None,fig=None):
    im= cv2.imread(os.path.join(img_prefix,img['file_name']))
    annIds = coco.getAnnIds(imgIds=img['id'], iscrowd=None)
    anns = coco.loadAnns(annIds)
    im = im[:, :, (2, 1, 0)]
    sizes = np.shape(im)
    mask = coco.annToMask(anns[0])
    height = float(sizes[0])
    width = float(sizes[1])
    if fig is None:
        raise(fig is not None,'fig is None')
    fig.set_size_inches(width / 100, height / 100)
    ax = plt.Axes(fig, [0., 0., 1., 1.])
    ax.set_axis_off()
    fig.add_axes(ax)
    ax.imshow(im)
    objs = []
    for ann in anns:
        name = classes[ann['category_id']]
        if name in SelectedCats:
            if 'bbox' in ann:
                bbox = ann['bbox']
                xmin = int(bbox[0])
                ymin = int(bbox[1])
                xmax = int(bbox[2] + bbox[0])
                ymax = int(bbox[3] + bbox[1])
                obj = [name, 1.0, xmin, ymin, xmax, ymax]
                objs.append(obj)
                ax.add_patch(plt.Rectangle((xmin, ymin), xmax - xmin, ymax - ymin,
                                           fill=False, linewidth=1.0, color='g'))
                ax.annotate(name, (xmin,ymin), color='g',
                            weight='bold', fontsize=6, ha='center', va='center')
#         mask += coco.annToMask(ann)
        
        mask = np.maximum(coco.annToMask(ann), mask)

    im[..., 2] = np.where(mask == 1, 255, im[..., 2])
    print("{} find {} objects".format(img['file_name'],len(objs)))
    plt.axis('off')
    # plt.tight_layout()
    # plt.draw()
    # plt.savefig(im_output, dpi=100)
    plt.imshow(im)
    plt.show() #在plt.ion()模式下，不会阻断
    plt.waitforbuttonpress() #阻断，等待鼠标点击或者键盘按键后继续运行
    plt.clf()

def showbycv(coco, img_prefix, img, classes, SelectedCats=None):
    catagory_path=base_path+"DFG-tsd-category-info/"
    I= cv2.imread(os.path.join(img_prefix,img['file_name']))
    mask = np.zeros((img['height'],img['width']))
    annIds = coco.getAnnIds(imgIds=img['id'], iscrowd=None)
    anns = coco.loadAnns(annIds)
    objs = []
    for ann in anns:
        name = classes[ann['category_id']]
        
        if name in SelectedCats:
            if 'bbox' in ann:
            
                bbox = ann['bbox']
                xmin = int(bbox[0])
                ymin = int(bbox[1])
                xmax = int(bbox[2] + bbox[0])
                ymax = int(bbox[3] + bbox[1])
                obj = [name, 1.0, xmin, ymin, xmax, ymax]
                objs.append(obj)
                cv2.rectangle(I, (xmin, ymin), (xmax, ymax), (255, 0, 0))
                cv2.putText(I, name, (xmin, ymin), 3, 0.5, (0, 0, 255))
                
                norm_sign_path=os.path.join(catagory_path,name,"*.png")
                norm_sign_path=random.choice(glob.glob(norm_sign_path))
                print(norm_sign_path)
                
                norm_sign=cv2.imread(norm_sign_path)
                dim = (int((xmax-xmin)/2), int((ymax-ymin)/2))
                # resize image
                norm_sign = cv2.resize(norm_sign, dim, interpolation = cv2.INTER_AREA)
                try:
                    I[ymin:ymin+norm_sign.shape[0], xmax:xmax+norm_sign.shape[1]] = norm_sign
                except Exception as e:
                    print(e)
                    continue
#         mask += coco.annToMask(ann)   
        mask = np.maximum(coco.annToMask(ann), mask)
        
    I[..., 2] = np.where(mask == 1, 255, I[..., 2])
    cv2.imshow("img", I)
    cv2.waitKey(0) #0表示等待键盘按键

def catid2name(coco):
    classes = dict()
    for cat in coco.dataset['categories']:
        classes[cat['id']] = cat['name']
        print(str(cat['id'])+":"+cat['name'])
    return classes

if __name__=="__main__":
    
    annFile =difficult_labels
    img_prefix=imgs_path
    coco = COCO(annFile)
    coco_catid2name = catid2name(coco)
    fig = plt.figure()
    plt.ion()  # matplotlib interactivate mode 当交互模式打开后，plt.show()不会阻断运行
    for img_id in coco.imgs:
        img=coco.imgs[img_id]
        # showimg(coco,img_prefix,img,SelectedCats) 
        # 通多opencv交互显示图像和标注；按下键盘回车或者空格自动显示下一张图像
        showbycv(coco,img_prefix,img,coco_catid2name,SelectedCats) 
        # 通过matplotlib.pylot交互显示图像和标注；点击鼠标或者键盘自动显示下一张图像
#         showbyplt(coco, img_prefix, img, coco_catid2name, SelectedCats,fig=fig)